In [2]:
from transformers import GPT2LMHeadModel, GPT2Tokenizer
from bertviz import head_view, model_view
import numpy as np
import torch

In [4]:
def break_attn_heads_by_layer(zero_type, model, share, layer):
    """
    set certain percentage attention heads to zero at specific layer
    return the modified model
    :param zero_type: the type for zeroing attention heads,
                      'random', 'first' and 'shuffle' are supported
    :type zero_type: str
    :param model: the oringal GPT-2 model to be modified
    :type model: transformers.modeling_gpt2.GPT2LMHeadModel
    :param share: % of attention heads to be zeroed,
                  25%, 50%, and 100% are supported
    :type share: int
    :param layer: the specific layer to be modified,
                  ranging from 0 to 11
    :type layer: int

    :return: the modified model
    :rtype: transformers.modeling_gpt2.GPT2LMHeadModel
    """
    # zeroing both weights and bias
    head_offsets = [1536, 1536+64, 1536+128, 1536+192, 1536+256,
                    1536+320, 1536+384, 1536+448, 1536+512,
                    1536+576, 1536+640, 1536+704]
    batch = 64
    with torch.no_grad():
        if zero_type == 'random':
            np.random.seed(42)
            torch.manual_seed(42)
            # Serguei's approach to reduce running time
            for head in head_offsets:
                # update to unique random integers
                rnd_index = np.random.choice(range(head, head+64), int(batch*(share/100)), replace=False)
                for row in range(0,model.transformer.h[layer].attn.c_attn.weight.size()[0]):
                    model.transformer.h[layer].attn.c_attn.weight[row][rnd_index] = \
                        model.transformer.h[layer].attn.c_attn.weight[row][rnd_index].mul(0.0)
                    model.transformer.h[layer].attn.c_attn.bias[rnd_index] = \
                        model.transformer.h[layer].attn.c_attn.bias[rnd_index].mul(0.0)
            return model
        elif zero_type == 'first':
            offset = int(batch*(share/100))
            for head in head_offsets:
                for row in range(0,model.transformer.h[layer].attn.c_attn.weight.size()[0]):
                    model.transformer.h[layer].attn.c_attn.weight[row][head:head+offset] = \
                        model.transformer.h[layer].attn.c_attn.weight[row][head:head+offset].mul(0.0)
                    model.transformer.h[layer].attn.c_attn.bias[head:head+offset] = \
                        model.transformer.h[layer].attn.c_attn.bias[head:head+offset].mul(0.0)
            return model
        elif zero_type == 'shuffle':
            offset = int(64*(share/100))
            for head in head_offsets:
                for row in range(0,model.transformer.h[layer].attn.c_attn.weight.size()[0]):
                    np.random.shuffle(model.transformer.h[layer].attn.c_attn.weight[row][head:head+offset])
                    np.random.shuffle(model.transformer.h[layer].attn.c_attn.bias[row][head:head+offset])
            return model
        else:
            raise ValueError("zeroing type is not supported!")

def accumu_model_driver(model, share, zero_style, num_layers):
    """
    the driver function for breaking GPT-2 model
    :param model: the oringal GPT-2 model to be modified
    :type model: transformers.modeling_gpt2.GPT2LMHeadModel
    :param share: % of attention heads to be zeroed
    :type share: int
    :param zero_style: the style of zeroing attention heads
    :type zero_style: str
    :param num_layers: numer of layers to be zeroed
    :type num_layers: int
    :return: the modified model
    :rtype: transformers.modeling_gpt2.GPT2LMHeadModel
    """
    if num_layers > 13:
        raise ValueError("GPT-2 model only has 12 layers")
    for i in range(0, num_layers):
        model = break_attn_heads_by_layer(zero_style, model, share, i)
    return model

In [23]:
model_con = GPT2LMHeadModel.from_pretrained("gpt2", output_attentions=True)
model_dem = GPT2LMHeadModel.from_pretrained("gpt2", output_attentions=True)
tokenizer = GPT2Tokenizer.from_pretrained("gpt2", do_lower_case=True)

# best pattern on ADReSS
layers = 9
share = 50
zero_style = "first"
model_dem = accumu_model_driver(model_dem, share, zero_style, layers)

In [24]:
# visualization of control model
text = "The little boy has climbed up, on a three legged stool to get some cookies from the jar in the cupboard."
inputs = tokenizer.encode_plus(text, return_tensors='pt', add_special_tokens=True)
input_ids = inputs['input_ids']
attention = model_con(input_ids)[-1]
input_id_list = input_ids[0].tolist() # Batch index 0
tokens = tokenizer.convert_ids_to_tokens(input_id_list)
head_view(attention, tokens)

<IPython.core.display.Javascript object>

In [17]:
inputs = tokenizer.encode_plus(text, return_tensors='pt', add_special_tokens=True)
input_ids = inputs['input_ids']
attention = model_dem(input_ids)[-1]
input_id_list = input_ids[0].tolist() # Batch index 0
tokens = tokenizer.convert_ids_to_tokens(input_id_list)
head_view(attention, tokens)

<IPython.core.display.Javascript object>